In [1]:
from tqdm import tqdm
from itertools import combinations
from pathlib import Path
import sys
import warnings
import logging
from pprint import pformat
import traceback
import os

import numpy as np
import pandas as pd
from pmdarima.arima import ARIMA, auto_arima
import tensorflow as tf
import tensorflow.keras as keras
from tensorflow.keras.models import load_model
from tensorflow.keras.layers import Input, LSTM, Dense
from tensorflow.keras.callbacks import ModelCheckpoint, TensorBoard
from tensorflow.keras.regularizers import l1_l2
import dynamic_yaml
import yaml

sys.path.append("/tf/correlation-coef-predict/ywt_library")
import data_generation
from data_generation import data_gen_cfg
from ywt_arima import arima_model, arima_err_logger_init

with open('../config/data_config.yaml') as f:
    data = dynamic_yaml.load(f)
    data_cfg = yaml.full_load(dynamic_yaml.dump(data))

warnings.simplefilter("ignore")
logging.basicConfig(level=logging.INFO)


# %load_ext pycodestyle_magic
# %pycodestyle_on --ignore E501
logging.info(pformat(data_cfg, indent=1, width=100, compact=True))

INFO:root:{'DATASETS': {'BITCOIN_NVDA': {'FILE_PATH': '/tf/correlation-coef-predict/dataset/bitcoin_nvda_20122022-pre.csv',
                               'OUTPUT_FILE_NAME_BASIS': 'bitcoin_nvda_20122022',
                               'TRAIN_SET': []},
              'PAPER_EVA_1': {'FILE_PATH': '/tf/correlation-coef-predict/dataset/sp500_hold_20082017-adj_close-pre.csv',
                              'OUTPUT_FILE_NAME_BASIS': 'paper_eva1',
                              'TEST_SET': ['PRGO', 'MRO', 'ADP', 'HCP', 'FITB', 'PEG', 'SYMC',
                                           'EOG', 'MDT', 'NI'],
                              'TRAIN_SET': ['CELG', 'PXD', 'WAT', 'LH', 'AMGN', 'AOS', 'EFX', 'CRM',
                                            'NEM', 'JNPR', 'LB', 'CTAS', 'MAT', 'MDLZ', 'VLO',
                                            'APH', 'ADM', 'MLM', 'BK', 'NOV', 'BDX', 'RRC', 'IVZ',
                                            'ED', 'SBUX', 'GRMN', 'CI', 'ZION', 'COO', 'TIF', 'RHT',

time: 1.95 s (started: 2022-11-15 10:35:20 +00:00)


# Prepare data

## Data implement & output setting & trainset setting

In [2]:
model_dir = Path('./save_models/')
lstm_log_dir = Path('./save_models/lstm_train_logs/')
res_dir = Path('./results/')
model_dir.mkdir(parents=True, exist_ok=True)
lstm_log_dir.mkdir(parents=True, exist_ok=True)
res_dir.mkdir(parents=True, exist_ok=True)

# setting of output files
save_corr_data = True
save_arima_resid_data = True
# data implement setting
data_implement = "SP500_20082017_FREQ_CLUSTER_LABEL_1"  # watch options by operate: print(data_cfg["DATASETS"].keys())
# train set setting
train_items_setting = "-train_train"  # -train_train|-train_all
# data split  period setting, only suit for only settings of Korean paper
data_split_settings = ["-data_sp_train", "-data_sp_dev", "-data_sp_test1", "-data_sp_test2", ]
# lstm_hyper_params
lstm_hyper_param = "-kS_hyper"

time: 906 µs (started: 2022-11-15 10:35:22 +00:00)


In [3]:
# data loading & implement setting
dataset_df = pd.read_csv(data_cfg["DATASETS"][data_implement]['FILE_PATH'])
dataset_df = dataset_df.set_index('Date')
all_set = list(dataset_df.columns)  # all data
train_set = data_cfg["DATASETS"][data_implement]['TRAIN_SET']
test_set = data_cfg['DATASETS'][data_implement]['TEST_SET'] if data_cfg['DATASETS'][data_implement].get('TEST_SET') else [p for p in all_set if p not in train_set]  # all data - train data
logging.info(f"===== len(train_set): {len(train_set)}, len(all_set): {len(all_set)}, len(test_set): {len(test_set)} =====")

# train items implement settings
items_implement = train_set if train_items_setting == "-train_train" else all_set
logging.info(f"===== len(train set): {len(items_implement)} =====")

# setting of name of output files and pictures title
output_file_name = data_cfg["DATASETS"][data_implement]['OUTPUT_FILE_NAME_BASIS'] + train_items_setting
logging.info(f"===== file_name basis:{output_file_name} =====")

# display(dataset_df)

INFO:root:===== len(train_set): 66, len(all_set): 76, len(test_set): 10 =====
INFO:root:===== len(train set): 66 =====
INFO:root:===== file_name basis:sp500_20082017_freq_cluster_label_1-train_train =====


time: 22.6 ms (started: 2022-11-15 10:35:22 +00:00)


## Load or Create Correlation Data

In [5]:
corr_data_dir = Path(data_cfg["DIRS"]["PIPELINE_DATA_DIR"])/f"{output_file_name}-corr_data"
corr_data_dir.mkdir(parents=True, exist_ok=True)
data_length = int(len(dataset_df)/data_gen_cfg["CORR_WINDOW"])*data_gen_cfg["CORR_WINDOW"]
corr_ser_len_max = int((data_length-data_gen_cfg["CORR_WINDOW"])/data_gen_cfg["CORR_STRIDE"])

train_df_path = corr_data_dir/f"{output_file_name}-corr_train.csv"
dev_df_path = corr_data_dir/f"{output_file_name}-corr_dev.csv"
test1_df_path = corr_data_dir/f"{output_file_name}-corr_test1.csv"
test2_df_path = corr_data_dir/f"{output_file_name}-corr_test2.csv"
all_corr_df_paths = dict(zip(["train_df", "dev_df", "test1_df", "test2_df"],
                             [train_df_path, dev_df_path, test1_df_path, test2_df_path]))
if all([df_path.exists() for df_path in all_corr_df_paths.values()]):
    corr_datasets = [pd.read_csv(df_path).set_index("items") for df_path in all_corr_df_paths.values()]
else:
    corr_datasets = data_generation.gen_train_data(items_implement, raw_data_df=dataset_df, corr_df_paths=all_corr_df_paths, corr_ser_len_max=corr_ser_len_max, save_file=save_corr_data)

time: 73.7 ms (started: 2022-11-15 10:36:25 +00:00)


# ARIMA model

In [7]:
arima_result_dir = Path(data_cfg["DIRS"]["PIPELINE_DATA_DIR"])/f"{output_file_name}-arima_res"
arima_result_dir.mkdir(parents=True, exist_ok=True)
arima_result_path_basis = arima_result_dir/f'{output_file_name}.csv'
arima_result_paths = []
arima_result_types = ["-arima_model_info", "-arima_output", "-arima_resid"]
arima_err_logger_init(Path(os.path.abspath(''))/f"save_models")


for data_sp_setting in data_split_settings:
    for arima_result_type in arima_result_types:
        arima_result_paths.append(arima_result_dir/f'{output_file_name}{arima_result_type}{data_sp_setting}.csv')

if all([df_path.exists() for df_path in arima_result_paths]):
    pass
else:
    for (data_sp_setting, dataset) in tqdm(zip(data_split_settings, corr_datasets)):
        arima_model(dataset, arima_result_path_basis=arima_result_path_basis, data_split_setting=data_sp_setting, save_file=save_arima_resid_data)

0it [00:00, ?it/s]
0it [00:00, ?it/s]
1it [00:00,  5.30it/s]
2it [00:00,  5.45it/s]
3it [00:00,  5.37it/s]
4it [00:00,  5.67it/s]
5it [00:00,  6.39it/s]
6it [00:01,  6.27it/s]
7it [00:01,  6.43it/s]
8it [00:01,  5.83it/s]
9it [00:01,  5.52it/s]
10it [00:01,  5.51it/s]
11it [00:01,  6.10it/s]
12it [00:02,  6.34it/s]
13it [00:02,  6.14it/s]
14it [00:02,  5.97it/s]
15it [00:02,  5.70it/s]
16it [00:02,  5.64it/s]
17it [00:02,  6.12it/s]
18it [00:03,  5.70it/s]
19it [00:03,  5.75it/s]
20it [00:03,  5.60it/s]
21it [00:03,  5.33it/s]
22it [00:03,  5.24it/s]
23it [00:04,  5.11it/s]
24it [00:04,  5.11it/s]
25it [00:04,  5.25it/s]
26it [00:04,  5.32it/s]
27it [00:04,  5.30it/s]
28it [00:05,  4.90it/s]
29it [00:05,  4.96it/s]
30it [00:05,  4.97it/s]
31it [00:05,  5.26it/s]
32it [00:05,  5.63it/s]
33it [00:05,  5.60it/s]
34it [00:06,  5.88it/s]
35it [00:06,  5.58it/s]
36it [00:06,  5.46it/s]
37it [00:06,  5.97it/s]
38it [00:06,  5.57it/s]
39it [00:07,  5.42it/s]
40it [00:07,  5.43it/s]
41it [00:07

time: 2h 10min 30s (started: 2022-11-15 10:36:40 +00:00)


# LSTM

## settings of input data of LSTM

In [11]:
# Dataset.from_tensor_slices(dict(pd.read_csv(f'./dataset/after_arima/arima_resid_train.csv')))
arima_result_dir = Path(data_cfg["DIRS"]["PIPELINE_DATA_DIR"])/f"{output_file_name}-arima_res"
lstm_train_X = pd.read_csv(arima_result_dir/f'{output_file_name}-arima_resid-data_sp_train.csv', index_col="items").iloc[::, :-1]
lstm_train_Y = pd.read_csv(arima_result_dir/f'{output_file_name}-arima_resid-data_sp_train.csv', index_col="items").iloc[::, -1]
lstm_dev_X = pd.read_csv(arima_result_dir/f'{output_file_name}-arima_resid-data_sp_dev.csv', index_col="items").iloc[::, :-1]
lstm_dev_Y = pd.read_csv(arima_result_dir/f'{output_file_name}-arima_resid-data_sp_dev.csv', index_col="items").iloc[::, -1]
lstm_test1_X = pd.read_csv(arima_result_dir/f'{output_file_name}-arima_resid-data_sp_test1.csv', index_col="items").iloc[::, :-1]
lstm_test1_Y = pd.read_csv(arima_result_dir/f'{output_file_name}-arima_resid-data_sp_test1.csv', index_col="items").iloc[::, -1]
lstm_test2_X = pd.read_csv(arima_result_dir/f'{output_file_name}-arima_resid-data_sp_test2.csv', index_col="items").iloc[::, :-1]
lstm_test2_Y = pd.read_csv(arima_result_dir/f'{output_file_name}-arima_resid-data_sp_test2.csv', index_col="items").iloc[::, -1]

lstm_train_X = lstm_train_X.values.reshape(-1, 20, 1)
lstm_train_Y = lstm_train_Y.values.reshape(-1, 1)
lstm_dev_X = lstm_dev_X.values.reshape(-1, 20, 1)
lstm_dev_Y = lstm_dev_Y.values.reshape(-1, 1)
lstm_test1_X = lstm_test1_X.values.reshape(-1, 20, 1)
lstm_test1_Y = lstm_test1_Y.values.reshape(-1, 1)
lstm_test2_X = lstm_test2_X.values.reshape(-1, 20, 1)
lstm_test2_Y = lstm_test2_Y.values.reshape(-1, 1)

time: 140 ms (started: 2022-11-15 13:17:22 +00:00)


## settings of LSTM

In [12]:
if lstm_hyper_param == "-kS_hyper":
    lstm_layer = LSTM(units=10, kernel_regularizer=l1_l2(0.2, 0.0), bias_regularizer=l1_l2(0.2, 0.0), activation="tanh", dropout=0.1, name=f"lstm{lstm_hyper_param}")  # LSTM hyper params from 【Something Old, Something New — A Hybrid Approach with ARIMA and LSTM to Increase Portfolio Stability】

time: 368 ms (started: 2022-11-15 13:17:23 +00:00)


2022-11-15 13:17:24.022623: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:975] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-11-15 13:17:24.027069: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:975] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-11-15 13:17:24.027296: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:975] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-11-15 13:17:24.027973: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags

In [13]:
def double_tanh(x):
    return (tf.math.tanh(x) *2)


def build_many_one_lstm():
    inputs = Input(shape=(20, 1))
    lstm_1 = lstm_layer(inputs)
    outputs = Dense(units=1, activation=double_tanh)(lstm_1)
    return keras.Model(inputs, outputs, name=f"lstm1_fc1{lstm_hyper_param}")


opt = keras.optimizers.Adam(learning_rate=0.0001)
lstm_model = build_many_one_lstm()
lstm_model.summary()
lstm_model.compile(loss='mean_squared_error', optimizer=opt, metrics=['mse', 'mae'])

Model: "lstm1_fc1-kS_hyper"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 20, 1)]           0         
                                                                 
 lstm-kS_hyper (LSTM)        (None, 10)                480       
                                                                 
 dense (Dense)               (None, 1)                 11        
                                                                 
Total params: 491
Trainable params: 491
Non-trainable params: 0
_________________________________________________________________
time: 405 ms (started: 2022-11-15 13:17:30 +00:00)


In [ ]:
res_csv_path = res_dir/f'{output_file_name}{lstm_hyper_param}_lstm_evaluation.csv'
res_csv_path.touch(exist_ok=True)
with open(res_csv_path, 'r+') as f:
    if not f.read():
        f.write("epoch,TRAIN_MSE,DEV_MSE,TEST1_MSE,TEST2_MSE,TRAIN_MAE,DEV_MAE,TEST1_MAE,TEST2_MAE")

res_df = pd.read_csv(res_csv_path)
saved_model_list = [int(p.stem[p.stem.find("epoch")+len("epoch"):]) for p in model_dir.glob('*.h5')]
model_cbk = TensorBoard(log_dir=lstm_log_dir)
epoch_start = max(saved_model_list) if saved_model_list else 1
max_epoch = 5000
batch_size = 64

try:
    for epoch_num in tqdm(range(epoch_start, max_epoch)):
        if epoch_num > 1:
            lstm_model = load_model(model_dir/f"{output_file_name}{lstm_hyper_param}-epoch{epoch_num - 1}.h5", custom_objects={'double_tanh':double_tanh})

        save_model = ModelCheckpoint(model_dir/f"{output_file_name}{lstm_hyper_param}-epoch{epoch_num}.h5",
                                                     monitor='loss', verbose=1, mode='min', save_best_only=False)
        lstm_model.fit(lstm_train_X, lstm_train_Y, epochs=1, batch_size=batch_size, shuffle=True, callbacks=[model_cbk, save_model])

        # test the model
        score_train = lstm_model.evaluate(lstm_train_X, lstm_train_Y)
        score_dev = lstm_model.evaluate(lstm_dev_X, lstm_dev_Y)
        score_test1 = lstm_model.evaluate(lstm_test1_X, lstm_test1_Y)
        score_test2 = lstm_model.evaluate(lstm_test2_X, lstm_test2_Y)
        res_each_epoch_df = pd.DataFrame(np.array([epoch_num, score_train[0], score_dev[0],
                                                   score_test1[0], score_test2[0],
                                                   score_train[1], score_dev[1],
                                                   score_test1[1], score_test2[1]]).reshape(-1, 9),
                                        columns=["epoch", "TRAIN_MSE", "DEV_MSE", "TEST1_MSE",
                                                 "TEST2_MSE", "TRAIN_MAE", "DEV_MAE",
                                                 "TEST1_MAE", "TEST2_MAE"])
        res_df = pd.concat([res_df, res_each_epoch_df])
        if (res_df.shape[0] % 100) == 0:
            res_df.to_csv(res_csv_path, index=False)  # insurance for 『finally』 part doesent'work
except Exception as e:
    error_class = e.__class__.__name__  # 取得錯誤類型
    detail = e.args[0]  # 取得詳細內容
    cl, exc, tb = sys.exc_info()  # 取得Call Stack
    last_call_stack = traceback.extract_tb(tb)[-1]  # 取得Call Stack的最後一筆資料
    file_name = last_call_stack[0]  # 取得發生的檔案名稱
    line_num = last_call_stack[1]  # 取得發生的行號
    func_name = last_call_stack[2]  # 取得發生的函數名稱
    err_msg = "File \"{}\", line {}, in {}: [{}] {}".format(file_name, line_num, func_name, error_class, detail)
    print(err_msg)
else:
    pass
finally:
    res_df.to_csv(res_csv_path, index=False)

  0% 0/4999 [00:00<?, ?it/s]2022-11-15 13:17:40.580999: I tensorflow/stream_executor/cuda/cuda_dnn.cc:384] Loaded cuDNN version 8100


 19/168 [==>...........................] - ETA: 0s - loss: 4.1038 - mse: 0.2357 - mae: 0.3927  

2022-11-15 13:17:41.007911: I tensorflow/stream_executor/cuda/cuda_blas.cc:1786] TensorFloat-32 will be used for the matrix multiplication. This will only be logged once.


154/168 [==========================>...] - ETA: 0s - loss: 4.0405 - mse: 0.2381 - mae: 0.3909
Epoch 1: saving model to save_models/sp500_20082017_freq_cluster_label_1-train_train-kS_hyper-epoch1.h5
336/336 [==============================] - 1s 2ms/step - loss: 4.0352 - mse: 0.3207 - mae: 0.4477


  0% 1/4999 [00:05<7:01:34,  5.06s/it]

...

152/168 [==========================>...] - ETA: 0s - loss: 0.2094 - mse: 0.2057 - mae: 0.3562
Epoch 1: saving model to save_models/sp500_20082017_freq_cluster_label_1-train_train-kS_hyper-epoch4451.h5
336/336 [==============================] - 1s 2ms/step - loss: 0.3232 - mse: 0.3195 - mae: 0.4454


 89% 4451/4999 [5:35:17<41:34,  4.55s/it]

160/168 [===========================>..] - ETA: 0s - loss: 0.2127 - mse: 0.2090 - mae: 0.3573
Epoch 1: saving model to save_models/sp500_20082017_freq_cluster_label_1-train_train-kS_hyper-epoch4452.h5
336/336 [==============================] - 1s 2ms/step - loss: 0.3246 - mse: 0.3210 - mae: 0.4451


 89% 4452/4999 [5:35:23<43:48,  4.81s/it]

165/168 [============================>.] - ETA: 0s - loss: 0.2123 - mse: 0.2085 - mae: 0.3579
Epoch 1: saving model to save_models/sp500_20082017_freq_cluster_label_1-train_train-kS_hyper-epoch4453.h5
 30/336 [=>............................] - ETA: 0s - loss: 0.2348 - mse: 0.2311 - mae: 0.3725